# Обработка данных с MS_DOS

Выделить чистый тензо сигнал 

In [23]:
import pandas as pd
import numpy as np
from scipy.optimize import minimize


Данные из файла в ёксили или csv

In [24]:
df_dev_0 = pd.read_excel('2023-08.xlsx', names=[
                                                        'Datetime',
                                                        'TempSens',
                                                        'tenzo',
                                                        'Moisture',
                                                        'BaseTemp',
                                                        'AirTemp'], header=1)

Выводим первые пять строк

In [25]:
df_dev_0.head()

Datetime  TempSens    tenzo  Moisture  BaseTemp  AirTemp
0 2023-08-26 00:02:36   12.3483  2084660     66.71   12.2389  11.9362
1 2023-08-26 00:03:31   12.3384  2084660     66.70   12.2342  11.9316
2 2023-08-26 00:04:26   12.3294  2084662     66.85   12.2306  11.9264
3 2023-08-26 00:05:21   12.3236  2084665     66.91   12.2281  11.9199
4 2023-08-26 00:06:16   12.3187  2084667     66.82   12.2247  11.9108

# Алгоритм преобразования тензо сигнала от паразитных зависимостей:
1. Убираем зависимость от Влажности $level (H)$ : дисперсия на этом шаге = 40793 
2. Убираем зависимости от Температур $level(AirTemp),level(TempSens)$: дисперсия на этом шаге = 17563 
3. Найдем при помощи уравнений Мат. Физики рапределение температуры в тезнодатчике U(x,t) : дисперсия на этом шаге = 13640
4. Ищем зависимость $level(U(x,t))$ : дисперсия на этом шаге = 6210
5. Наложим Кравые условия (Граничные условия) на $U(x,t) => U'(0,t) = h[U(0,t)-U_{0}] $ и  $ U'(l,t) = -h[U(l,t)-U_{0}]$ : дисперсия на этом шаге = 5980
6. Попытался продифферинцировать данные: Результат только дал дифферинцал Влажности по времени dH/dt : дисперсия на этом шаге = 5930
7. Сделал еще пару шагов с дифференцированием влажности, дисперсия снизилась но не значительно: дисперсия на этом шаге = 5912
8. Методы Sklear позволяют снизить дисперсию: дисперсия на этом шаге = 5670
9. Добился значения дисперсии = 5617 подобравь функцию для $[level(\frac{\mathrm d H(t)}{\mathrm d t}) = level - K_{1} Sklearn( \frac{\mathrm d H(t)}{\mathrm d t} )^2 - K_{2} Sklearn(\frac{\mathrm d H(t)}{\mathrm d t} )]$, но не могу понять почему преобразованный уровень все время скачет.  
10. Применил методы фильтрации сигнала, а именно Скользящие среднее(есть минус появляется сдвиг во времени) : дисперсия на этом шаге = 5440
11. Продолжаю дальше избавляться от зависимостей 


# Sklearn
Методы уменьшения размеров данных при помоши sklearn
(поробую сделать может поможет)

In [26]:
from sklearn.preprocessing import StandardScaler
from sklearn.cluster import KMeans


numerical_cols = ['TempSens', 'tenzo', 'Moisture', 'BaseTemp', 'AirTemp']
numerical_data = df_dev_0[numerical_cols]


scaler = StandardScaler()
scaled_data = scaler.fit_transform(numerical_data)


kmeans = KMeans(n_clusters=3)
cluster = kmeans.fit_predict(scaled_data)


df_dev_0['Cluster'] = cluster



c:\Users\saryc\AppData\Local\Programs\Python\Python311\Lib\site-packages\sklearn\cluster\_kmeans.py:1412: FutureWarning:

The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning



# PCA (Principal Component Analysis)

In [27]:
from sklearn.decomposition import PCA
import seaborn as sns
import matplotlib.pyplot as plt

pca2D = PCA(n_components=2)
pca_2D = pca2D.fit_transform(scaled_data)
pca2D_df = pd.DataFrame(data=pca_2D, columns=['tenzo', 'Moisture'])


pca2D_df['cluster'] = cluster
# print('var_tenzo = ',np.var(pca2D_df['tenzo']))

# sns.scatterplot(x='Moisture', y='tenzo', hue='cluster', data=pca2D_df)
# plt.legend()
# plt.grid(which = "both")
# plt.minorticks_on()
# plt.tick_params(which = "minor", bottom = False, left = False)
# plt.title("PCA")
# plt.show()

In [28]:

def objective_function(K):
                              
    U_l2_t = df_dev_0['TempSens'] + K[0] * (df_dev_0['BaseTemp'] + df_dev_0['AirTemp'] - 2 * df_dev_0['TempSens']) + K[1]  
    
    level_u = df_dev_0['tenzo'] - K[3] * U_l2_t  
    
    U_0_t = K[4] * (df_dev_0['BaseTemp'] - df_dev_0['TempSens'])
    level_U_0_t = level_u - U_0_t ** 2 * K[5] - U_0_t * K[6]
    
    U_L_t = - K[7]*(df_dev_0['AirTemp'] - df_dev_0['TempSens'])
    level_U_L_t =level_U_0_t  - U_L_t ** 2 * K[8]- U_L_t*K[9]  
    
    level_TempAir = level_U_L_t - K[10] * df_dev_0['AirTemp']
    
    level_TempSens = level_TempAir - df_dev_0['TempSens']**2*K[11] - df_dev_0['TempSens']*K[12]
    
    level_BaseTemp =  level_TempSens + K[13]*df_dev_0['BaseTemp'] ** 2 + K[14]*df_dev_0['BaseTemp']  
    
    level_H = level_BaseTemp - K[15] * df_dev_0['Moisture'] 
   
    H_T_sens = df_dev_0['Moisture'] + K[16]*U_L_t
    level_H_T = level_H - H_T_sens ** 2 *K[17] - H_T_sens *K [18]
    

    dHdt = np.gradient(df_dev_0['Moisture'], 50,edge_order=1)
    
    level_dHdt = level_H_T - dHdt*K[19]
    
    dH_T_sensdt = np.gradient(H_T_sens, 50,edge_order=1)
    level_dH_T_sensdt = level_dHdt + dH_T_sensdt*K[20]
    

    print('level',level_dH_T_sensdt)

    
    var_level = np.var(level_dH_T_sensdt)
    
    return  var_level

# Задайте начальные значения для K

initial_guess = [10.68, 31.13,
                 10,22, 10.41, 12,15,14, 5,
                 8,9, 10, 2,3, 4,20,10,10,
                 10,100,100,100]

print('Колличество K: ',len(initial_guess)-1)
# Минимизируйте функцию с помощью метода оптимизации

result = minimize(objective_function, initial_guess, method='BFGS')

optimal_K = result.x
optimal_scalar_value = objective_function(optimal_K)
# Выведите оптимальные значения
print('Оптимальные значения K:',pd.DataFrame(optimal_K))
print('Изначальное значение Дисперсии:', np.var(df_dev_0['tenzo']))
print('Оптимальные значения дисперсии:',optimal_scalar_value )


Колличество K:  21
level 0       1.925113e+06
1       1.926992e+06
2       1.927943e+06
3       1.927555e+06
4       1.926321e+06
            ...     
8169    2.045911e+06
8170    2.045507e+06
8171    2.043524e+06
8172    2.042646e+06
8173    2.039381e+06
Length: 8174, dtype: float64
level 0       1.925113e+06
1       1.926992e+06
2       1.927943e+06
3       1.927555e+06
4       1.926321e+06
            ...     
8169    2.045911e+06
8170    2.045507e+06
8171    2.043524e+06
8172    2.042646e+06
8173    2.039381e+06
Length: 8174, dtype: float64
level 0       1.925113e+06
1       1.926992e+06
2       1.927943e+06
3       1.927555e+06
4       1.926321e+06
            ...     
8169    2.045911e+06
8170    2.045507e+06
8171    2.043524e+06
8172    2.042646e+06
8173    2.039381e+06
Length: 8174, dtype: float64
level 0       1.925113e+06
1       1.926992e+06
2       1.927943e+06
3       1.927555e+06
4       1.926321e+06
            ...     
8169    2.045911e+06
8170    2.045507e+06
8171    2

level 0       1.947215e+06
1       1.948739e+06
2       1.949476e+06
3       1.949149e+06
4       1.948171e+06
            ...     
8169    2.059464e+06
8170    2.059134e+06
8171    2.057752e+06
8172    2.057112e+06
8173    2.054856e+06
Length: 8174, dtype: float64
level 0       1.947215e+06
1       1.948739e+06
2       1.949476e+06
3       1.949149e+06
4       1.948171e+06
            ...     
8169    2.059464e+06
8170    2.059134e+06
8171    2.057752e+06
8172    2.057112e+06
8173    2.054856e+06
Length: 8174, dtype: float64
level 0       1.947215e+06
1       1.948739e+06
2       1.949476e+06
3       1.949149e+06
4       1.948171e+06
            ...     
8169    2.059464e+06
8170    2.059134e+06
8171    2.057752e+06
8172    2.057112e+06
8173    2.054856e+06
Length: 8174, dtype: float64
level 0       1.947215e+06
1       1.948739e+06
2       1.949476e+06
3       1.949149e+06
4       1.948171e+06
            ...     
8169    2.059464e+06
8170    2.059134e+06
8171    2.057752e+06
8172   

In [34]:
print('Оптимальные значения K:',pd.DataFrame(optimal_K))

Оптимальные значения K:              0
0     0.594801
1    15.203466
2    10.000000
3   -58.172025
4    -0.018255
5    24.457223
6   228.158510
7    22.708331
8    -0.443517
9  -227.639372
10  130.723033
11   -4.870893
12  117.947699
13   -2.383879
14   71.655288
15    3.813551
16    9.388446
17    0.003450
18   23.112803
19    4.263243
20   13.297064
21  100.000000


# Построение графика tenzo и сравнение с преобразованным вариантом level

In [30]:

def function(K):
    
    rainfall_constant = 0
    
    middle_index = len(df_dev_0['tenzo']) // 2
    rainfall_values = np.full(len(df_dev_0['tenzo']) - middle_index, rainfall_constant)
    df_dev_0['tenzo'].iloc[middle_index:] += rainfall_values
                                                  
    U_l2_t = df_dev_0['TempSens'] + K[0] * (df_dev_0['BaseTemp'] + df_dev_0['AirTemp'] - 2 * df_dev_0['TempSens']) + K[1]  
    print('U_l2_t', U_l2_t[0])
    level_u = df_dev_0['tenzo'] - K[3] * U_l2_t  
    print('level_u', level_u[0])
    U_0_t = K[4] * (df_dev_0['BaseTemp'] - df_dev_0['TempSens'])
    print('U_0_t', U_0_t[0])
   
    level_U_0_t = level_u - U_0_t ** 2 * K[5] - U_0_t * K[6]
    print('level_U_0_t', level_U_0_t[0])
    U_L_t = - K[7]*(df_dev_0['AirTemp'] - df_dev_0['TempSens'])
    print('U_L_t', U_L_t[0])
    level_U_L_t =level_U_0_t  - U_L_t ** 2 * K[8]- U_L_t*K[9]  
    print('level_U_L_t', level_U_L_t[0])
    level_TempAir = level_U_L_t - K[10] * df_dev_0['AirTemp']
    print('level_TempAir', level_TempAir[0])
    level_TempSens = level_TempAir - df_dev_0['TempSens']**2*K[11] - df_dev_0['TempSens']*K[12]
    print(' level_TempSens',  level_TempSens[0])
    level_BaseTemp =  level_TempSens + K[13]*df_dev_0['BaseTemp'] ** 2 + K[14]*df_dev_0['BaseTemp']  
    print('  level_BaseTemp',  level_BaseTemp[0])
    level_H = level_BaseTemp - K[15] * df_dev_0['Moisture'] 
    print('   level_H',  level_BaseTemp[0])
    H_T_sens = df_dev_0['Moisture'] + K[16]*U_L_t
    print('  H_T_sens',  H_T_sens[0])
    level_H_T = level_H - H_T_sens ** 2 *K[17] - H_T_sens *K [18] 
    print('  level_H_T',  level_H_T[0])
    dHdt = np.gradient(df_dev_0['Moisture'], 50,edge_order=1)
    print('  dHdt',  dHdt[0])
   
    level_dHdt = level_H_T - dHdt*K[19]
    print(' level_dHdt',  level_dHdt[0])
    dH_T_sensdt = np.gradient(H_T_sens, 50,edge_order=1)
    print('  dH_T_sensdt',   dH_T_sensdt[0])
   
    level_dH_T_sensdt = level_dHdt + dH_T_sensdt*K[20]
    
    print('level',level_dH_T_sensdt[0])

    
    return level_dH_T_sensdt

level_dHdt = function(result.x)

optimal_K_list = [optimal_K]
optimal_K_df = pd.DataFrame(optimal_K_list,columns=['K{}'.format(i) for i in range(0, 22)])
optimal_K_df.to_csv('K0.csv', mode='a', header=False, index=False)

# Построение графиков 

from scipy import signal
b, a = signal.butter(3, 0.05)

zi = signal.lfilter_zi(b, a)
z, _ = signal.lfilter(b, a, level_dHdt, zi=zi*level_dHdt[0])
z2, _ = signal.lfilter(b, a, z, zi=zi*z[0])
y = signal.filtfilt(b, a, level_dHdt)
print("var = ",np.var(y))


import plotly.graph_objects as go

fig = go.Figure()

fig.add_trace(go.Scatter(x=df_dev_0['Datetime'], y=df_dev_0['tenzo'], mode='lines', name='Tenzo Data'))
fig.add_trace(go.Scatter(x=df_dev_0['Datetime'], y=level_dHdt, mode='lines', name='Level Data', yaxis='y2'))
    
  
fig.update_layout(
    legend=dict(x=.8),
    title='График сравнения  Tenzo и Level',
    title_x=0.5,
    xaxis=dict(title='Datatime'),
    yaxis=dict(tickformat ='d',title='Tenzo Data', side='left'),
    yaxis2=dict(tickformat ='d',title='Level Data', overlaying='y', side='right'),
    hovermode="x",
    font=dict(size=14),
    margin=dict(l=100, r=100, t=50, b=50) 
    )
fig.show()



U_l2_t 27.241577668338145
level_u 2086244.6977384242
U_0_t 0.001997107637859312
level_U_0_t 2086244.2419837757
U_L_t 9.358103371982583
level_U_L_t 2088413.355360044
level_TempAir 2086853.0190982136
 level_TempSens 2086139.2818438318
  level_BaseTemp 2086659.1809003511
   level_H 2086659.1809003511
  H_T_sens 154.5680520202318
  level_H_T 2082749.8422432602
  dHdt -0.0001999999999998181
 level_dHdt 2082749.8430959089
  dH_T_sensdt -0.0227987709637091
level 2082749.5399391947
var =  5846.104794135946


C:\Users\saryc\AppData\Local\Temp\ipykernel_17360\1518330121.py:7: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



# Построение на одной оси tenzo и level

In [31]:

fig = go.Figure()

fig.add_trace(go.Scatter(x=df_dev_0['Datetime'], y=df_dev_0['tenzo'], mode='lines', name='Tenzo Data'))
fig.add_trace(go.Scatter(x=df_dev_0['Datetime'], y=level_dHdt, mode='lines', name='Level Data'))

fig.update_layout(
    title='График сравнения  Tenzo и Level',
    title_x=0.5,
    xaxis=dict(title='Datatime'),
    yaxis=dict(tickformat ='d',title='Tenzo Data', side='left'),
    yaxis2=dict(tickformat ='d',title='Level Data', overlaying='y', side='right'),
    font=dict(size=14),
    hovermode="x",
    margin=dict(l=120, r=100, t=50, b=50) 
    )

fig.show()

# Комментарии к результатам на графике:

1. Разница между уровнями составляет: delta_tenzo = 1080 и  delta_level = 395
2. Добавил имитацию дождя к данным, регистрируется хорошо без сдвигов во времени 
3. Разница между уровнями составляет 40.37 (значение 1 дождя составляет 400 веса ). Проверено в ёксиле 
4. В случае добвления интегрирования или применения методов фильтрации (Скользящие средннее) у нас происходит смещение данных на 9-10 минут, что является недопустимым при регламенте в 5 минут.
5. Задержка 7 минут, но дисперсия 5440. Разница 418.
6. нужно провести тесты на других данных



Корелляция между Tenzo и преобразованным level:

In [32]:
corr = np.corrcoef(df_dev_0['tenzo'],level_dHdt,rowvar=False)
print('Коэффициент корелляции = ',corr[0,1])

Коэффициент корелляции =  0.2971119978451474
